In [ ]:
import numpy as np 
import matplotlib.pyplot as plt

In [ ]:
#SATURN AND MIMAS INITIAL POSITIONS AND VELOCITIES
mSat=5.69*10**26
#mSat=10**11
#mMimas=10**4
mMimas=3.75*10**23 #originally 3.75*10**19, exaggerated for effect 
G=6.67*10**-11
dSaturn_Mimas = 1.85*10**8

In [ ]:
#r=rs-rp=20
#rCM=(rp*mp+rs*ms)/(mp+ms)

rSat_rCM=dSaturn_Mimas*mMimas/(mMimas+mSat)
#rsrcm ~= <2e-2,0>

rSat=np.array([-rSat_rCM,0])
rMimas=np.array([dSaturn_Mimas-rSat_rCM,0])

mSat=5.69*10**26
angular_v=np.sqrt(G*(mSat+mMimas)/np.linalg.norm(rMimas-rSat)**3)
mag_vMimas = angular_v*np.linalg.norm(rMimas)
mag_vSat= angular_v*np.linalg.norm(rSat)

vMimasx=0
vMimasy=mag_vMimas

vMimas=np.array([vMimasx,vMimasy])

vSatx=0
vSaty=-mag_vSat

vSat=np.array([vSatx,vSaty])

y=np.concatenate([rSat,vSat,rMimas,vMimas])
print(y)

print(angular_v)
print(vSat,vMimas)

#THIS IS GOOD

In [ ]:
#PARTICLE INITIAL POSITIONS AND VELOCITIES
mParticles = 1
# G = 1

count=0 
rParticles = []
xdata = []
ydata = []
A_R = 1.37*10**8
B_R = 9.2*10**7
while count < 800:
    r_radius = np.random.random()
    r_theta  = np.random.random()
    radius = B_R + (A_R - B_R) * r_radius
    theta = r_theta * 2 * np.pi
    x = np.cos(theta)*radius
    y = np.sin(theta)*radius
    rParticles.append([x,y])
    xdata.append(x)
    ydata.append(y)
    count+=1
    
#     xsign=np.random.random()
#     ysign=np.random.random()
#     if xsign<=0.5:
#         x=20*np.random.random()
#     elif xsign>0.5:
#         x=-20*np.random.random()
#     if ysign<=0.5:
#         y=20*np.random.random()
#     elif ysign>0.5:
#         y=-20*np.random.random()
#     if B_R**2 <= x**2 + y**2 and x**2 + y**2 <= A_R**2:
#         rParticles.append([x,y])
#         xdata.append(x)
#         ydata.append(y)
#    count+=1

vParticles = []

for i in rParticles:
    angular_v=np.sqrt(G*(mSat+mMimas)/np.linalg.norm(i-rSat)**3)
    mag_vParticle = angular_v*np.linalg.norm(i)
    xVelocity = -angular_v * i[1]
    yVelocity = angular_v * i[0]
#    if i[1]>=0:
#         xVelocity = -mag_vParticle*np.cos(np.arctan(i[1]/i[0]))
#     elif i[1]<0:
#         xVelocity = mag_vParticle*np.cos(np.arctan(i[1]/i[0]))
#     if i[0]>=0:
#         yVelocity = mag_vParticle*np.sin(np.arctan(i[1]/i[0]))
#     elif i[0]<0:
#         yVelocity = -mag_vParticle*np.sin(np.arctan(i[1]/i[0]))
        
    vParticles.append([xVelocity,yVelocity])

z=np.concatenate([rParticles,vParticles])
print(rParticles[105])
print(vParticles[105])
rParticles = np.array(rParticles)
vParticles = np.array(vParticles)

In [ ]:
#DEFINING DIFFERENTIAL EQUATIONS (ERROR IN MIMASODE)
# mSat=10**11
Psquare=(4*np.pi**2)*((dSaturn_Mimas-rSat_rCM)**3)/(G*(mSat))
P=np.sqrt(Psquare)
print('T=',P)
#P should be approximately 0.184
dt=P/1000

#run to P/4:

t=0
tMax=P*1000
n=tMax/dt

def MimasODE(t,y):
    global G,mMimas,mSat
    rSat =y[0:2]
    vSat =y[2:4]
    rMimas =y[4:6] 
    vMimas =y[6:8] 

    drsdt=vSat
    drmdt=vMimas
    
    Fsat_mimas=-(rSat-rMimas)*G*mSat*mMimas/np.linalg.norm(rSat-rMimas)**3
   

    Fmimas_sat=-(rMimas-rSat)*G*mMimas*mSat/np.linalg.norm(rMimas-rSat)**3
  
    a_sat = (Fsat_mimas)/mSat
    
    a_mimas = (Fmimas_sat)/mMimas

    #dvdt = a 
    
    dvsdt = a_sat
    dvmdt = a_mimas

    return np.concatenate((drsdt,dvsdt,drmdt,dvmdt))

def ParticlesODE(t,z):
    global G,mMimas,mSat,mParticles
    
    rParticle = z[0:2]
    vParticle = z[2:4]
    
    drdt = vParticle
    
    Fparticle_saturn=-(rParticle-rSat)*G*mParticles*mSat/np.linalg.norm(rParticle-rSat)**3
    Fparticle_mimas=-(rParticle-rMimas)*G*mParticles*mMimas/np.linalg.norm(rParticle-rMimas)**3
    aParticle = (Fparticle_saturn + Fparticle_mimas)/mParticles
    
    dvdt = aParticle
    
    return np.concatenate((drdt,dvdt))

y=np.concatenate([rSat,vSat,rMimas,vMimas])
y0 = np.copy(y)
print(MimasODE(0,y))
print(y0)

#error is somewhere in the MimasSaturnKeplerODE function

In [ ]:
rParticles0 = np.copy(rParticles)
vParticles0 = np.copy(vParticles)
# plt.scatter(rParticles[:, 0],rParticles[:, 1], s=0.5,color='gold')
# plt.plot(xSat,ySat, 'or',ms=20)
# plt.plot(xMimas,yMimas, 'ob',ms=5)
# #plt.scatter(data_x,data_y)
# plt.xlim(-2.0 * dSaturn_Mimas, 2.0 * dSaturn_Mimas)
# plt.ylim(-2.0 * dSaturn_Mimas, 2.0 * dSaturn_Mimas)
# print(vParticles0)

In [ ]:
#ANIMATION
from matplotlib.animation import FFMpegWriter
%matplotlib qt
plt.show()
metadata = dict(title='Saturn, Mimas, and the A and B rings', artist='Brian Harris',comment='Single Orbit')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()
# xst=[-rSat_rCM] 
# yst=[0]
y = y0
# xmt=[20-rSat_rCM]
# ymt=[0]
# data_x=[]
# data_y=[]
rParticles = np.copy(rParticles0)
vParticles = np.copy(vParticles0)
print(vParticles)
n = 2000
for step in range(1,int(n)):
    
    rSat=y[0:2]
    rMimas=y[4:6]
#     xst.append(rSat[0])
#     yst.append(rSat[1])
#     xmt.append(rMimas[0])
#     ymt.append(rMimas[1])
    xSat = rSat[0]
    ySat = rSat[1]
    xMimas = rMimas[0]
    yMimas = rMimas[1]
    
    #dydt=KeplerODE(t,y)
    #y=y+dydt*dt
    
    f1 = MimasODE(t       ,y          )
    f2 = MimasODE(t+dt/2.0,y+f1*dt/2.0)
    f3 = MimasODE(t+dt/2.0,y+f2*dt/2.0)
    f4 = MimasODE(t+dt    ,y+f3*dt    )

    y = y + (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
    # print(xSat, ySat,xMimas, yMimas)
    
#     data_x.clear()
#     data_y.clear()
    
    for r in range(len(rParticles)):
        rParticle = rParticles[r]
        vParticle = vParticles[r] #np.array([0,0])
        z=np.concatenate((rParticle,vParticle))
#         data_x.append(rParticle[0])
#         data_y.append(rParticle[1])
        g1 = ParticlesODE(t       ,z          )
        g2 = ParticlesODE(t+dt/2.0,z+g1*dt/2.0)
        g3 = ParticlesODE(t+dt/2.0,z+g2*dt/2.0)
        g4 = ParticlesODE(t+dt    ,z+g3*dt    )
        
        z += (g1 + 2.0*g2 + 2.0 * g3 + g4) / 6.0 * dt
        
        rParticles[r] = z[0:2]
        vParticles[r] = z[2:4]
#     print("_______")
#     print(rParticles[50], rParticles[105])
#     print(vParticles[50], vParticles[105])
        
    t += dt
    if step%5==0:
        with writer.saving(fig, "animation1.mp4", dpi=200):
            plt.clf()
            plt.scatter(rParticles[:, 0],rParticles[:, 1], s=3,color='gold')
            plt.plot(xSat,ySat, 'or',ms=50)
            plt.plot(xMimas,yMimas, 'ob',ms=10)
            #pt.scatter(data_x,data_y)
            plt.xlim(-1.4 * dSaturn_Mimas, 1.4 * dSaturn_Mimas)
            plt.ylim(-1.4 * dSaturn_Mimas, 1.4 * dSaturn_Mimas)
            plt.xlabel('m')
            plt.ylabel('m')
            plt.draw()
            plt.pause(0.005)
            writer.grab_frame()
# plt.plot(xst,yst, 'or',ms=20)
# plt.plot(xmt,ymt, 'ob',ms=5)
#plt.scatter(data_x,data_y)
# plt.xlim(-25,25)
# plt.ylim(-25,25)
# plt.show()

In [ ]:
#EVERYTHING WORKS EXCEPT INITIAL VELOCITIES OF THE PARTICLES
#for some reason Mimas inexplicably gets launched???? must've unknowningly changed something 
#all fixed :>